In [1]:
#安裝套件
!pip install pyserini

In [2]:
import json
import pandas as pd
data = pd.read_csv('Pubmed 220 Train 2022-01-21.txt', sep="\n#", header=None)
data

<ipython-input-2-4a2fd3f6fc20>:3: ParserWarning: Falling back to the 'python' engine because the 'c' engine does not support regex separators (separators > 1 char and different from '\s+' are interpreted as regex); you can avoid this warning by specifying engine='python'.
  data = pd.read_csv('Pubmed 220 Train 2022-01-21.txt', sep="\n#", header=None)


0
0                                             ###24491034
1       BACKGROUND\tThe emergence of HIV as a chronic ...
2       BACKGROUND\tThis paper describes the design an...
3       METHODS\tThis study is designed as a randomise...
4       METHODS\tThe intervention group will participa...
...                                                   ...
732608  BACKGROUND\tThe cholesterol absorption inhibit...
732609  BACKGROUND\tThe milk fat globule membrane comp...
732610  OBJECTIVE\tTo evaluate in hypercholesterolemic...
732611  METHODS\tThe plant sterols in milk were determ...
732612  METHODS\tSixteen hypercholesterolemic adult me...

[732613 rows x 1 columns]

In [4]:
import json
import os.path
from tqdm import tqdm

pubmed_df = pd.DataFrame(columns=['id', 'content'])
count = 0
content = ""
id = ""
for i in tqdm(range(len(data[0]))):
  row = data[0][i]
  # 處理特殊字元
  if '###' in row:
    id = row.split('###')[1]
    content = ""
  # 單字整合成content
  else:
    row = row.replace("\t"," ")
    row = row.split(' ')[1:]

    for word in row:
      content += (word + " ")

    if i == len(data[0]) - 1 or '###' in data[0][i+1]:
      output = {
          "id": id,
          "contents": content
      }

      file_path = 'tests/resources/'+ str(id) +'.json'

      # 確保資料夾存在，如果不存在則創建
      os.makedirs(os.path.dirname(file_path), exist_ok=True)

      # 將資料寫入 JSON 檔案
      with open(file_path, "w") as t:
          json.dump(output, t)
      count += 1



100%|██████████| 732613/732613 [00:54<00:00, 13554.59it/s]


1. 使用 Python 命令執行 Pyserini 中的 index.lucene 模組
1. 指定要索引的文檔類型為 JSON 格式
1. 指定要索引的文檔目錄
1. 指定索引的輸出目錄和名稱
1. 指定文檔索引時使用的生成器。在此情況下，使用默認的 Lucene 文檔生成器
1. 指定用於索引的線程數。在此情況下，使用單線程
1. 指定存儲索引中的位置信息、文檔向量和原始文檔的選項


In [5]:
!python -m pyserini.index.lucene \
  --collection JsonCollection \
  --input contents \
  --index indexes/sample_collection_jsonl \
  --generator DefaultLuceneDocumentGenerator \
  --threads 1 \
  --storePositions --storeDocvectors --storeRaw

串流輸出內容已截斷至最後 5000 行。
2024-03-19 15:11:30,955 DEBUG [pool-2-thread-1] index.AbstractIndexer$IndexerThread (AbstractIndexer.java:175) - resources/19212856.json: 1 docs added.
2024-03-19 15:11:30,956 DEBUG [pool-2-thread-1] index.AbstractIndexer$IndexerThread (AbstractIndexer.java:175) - resources/25280603.json: 1 docs added.
2024-03-19 15:11:30,956 DEBUG [pool-2-thread-1] index.AbstractIndexer$IndexerThread (AbstractIndexer.java:175) - resources/9802752.json: 1 docs added.
2024-03-19 15:11:30,957 DEBUG [pool-2-thread-1] index.AbstractIndexer$IndexerThread (AbstractIndexer.java:175) - resources/22232563.json: 1 docs added.
2024-03-19 15:11:30,957 DEBUG [pool-2-thread-1] index.AbstractIndexer$IndexerThread (AbstractIndexer.java:175) - resources/10679756.json: 1 docs added.
2024-03-19 15:11:30,958 DEBUG [pool-2-thread-1] index.AbstractIndexer$IndexerThread (AbstractIndexer.java:175) - resources/19112278.json: 1 docs added.
2024-03-19 15:11:30,958 DEBUG [pool-2-thread-1] index.AbstractIndexe

In [6]:
!pip install faiss-cpu

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 27.0/27.0 MB 26.1 MB/s eta 0:00:00


In [7]:
from pyserini.search.lucene import LuceneSearcher
import time

# 初始化 LuceneSearcher 並指定索引目錄
searcher = LuceneSearcher('indexes/sample_collection_jsonl')

start = time.time()
# 進行搜索，搜索詞為 'cancer'，返回前 123456 個結果
hits = searcher.search('cancer', k=123456)
print(hits)
end = time.time()

for i in range(len(hits)):
    # 獲取文檔的檔名，此處假設檔名與文檔 ID 相同，並且位於指定目錄下的 resources 資料夾中
    filename = '/content/tests/resources/'+str(hits[i].docid)+'.json'
    f = open (filename, "r")

    data = json.loads(f.read())
    # 輸出搜索結果的文檔 ID、得分以及對應的內容
    print(f'{i+1:2} {hits[i].docid:4} {hits[i].score:.5f} \n {data}')



[<io.anserini.search.ScoredDoc at 0x7ee440fb4090 jclass=io/anserini/search/ScoredDoc jself=<LocalRef obj=0x55629bb915c0 at 0x7ee54dd140f0>>, <io.anserini.search.ScoredDoc at 0x7ee440fb4180 jclass=io/anserini/search/ScoredDoc jself=<LocalRef obj=0x55629bb915d0 at 0x7ee440f0b690>>, <io.anserini.search.ScoredDoc at 0x7ee440fb41d0 jclass=io/anserini/search/ScoredDoc jself=<LocalRef obj=0x55629bb915d8 at 0x7ee440f0af10>>, <io.anserini.search.ScoredDoc at 0x7ee440fb4220 jclass=io/anserini/search/ScoredDoc jself=<LocalRef obj=0x55629bb915e8 at 0x7ee440f0a7d0>>, <io.anserini.search.ScoredDoc at 0x7ee440fb42c0 jclass=io/anserini/search/ScoredDoc jself=<LocalRef obj=0x55629bb91600 at 0x7ee440f0b150>>, <io.anserini.search.ScoredDoc at 0x7ee440fb4270 jclass=io/anserini/search/ScoredDoc jself=<LocalRef obj=0x55629bb91610 at 0x7ee440f0aa30>>, <io.anserini.search.ScoredDoc at 0x7ee440fb4310 jclass=io/anserini/search/ScoredDoc jself=<LocalRef obj=0x55629bb91618 at 0x7ee440f0a0b0>>, <io.anserini.search

In [10]:
time_InvertedIndex = end - start
print("執行時間：%f 秒" % (time_InvertedIndex))

執行時間：0.692226 秒


In [11]:
import glob  # 導入 glob 模組，用於查找符合指定模式的檔案路徑

searchKey = 'cancer'

list = []  # 建立空的列表，用於儲存符合條件的資料
start = time.time()

# 使用 glob 模組找到指定目錄下所有以 .json 結尾的檔案路徑
all_file = glob.glob('/content/tests/resources/*.json')

for filename in all_file:
    with open(filename, 'r') as f:
        json_data = json.load(f)
        content = json_data['contents']
        # 檢查搜索關鍵字是否在內容中
        if searchKey in content:
            list.append(json_data)

end = time.time()

print(list)

# 輸出執行時間
excute_time = end - start
print("執行時間：%f 秒" % (excute_time))

[{'id': '25144625', 'contents': 'The Combined Aerobic and Resistance Exercise Trial tested different types and doses of exercise in breast cancer patients receiving chemotherapy . Here , we explore potential moderators of the exercise training responses . Breast cancer patients initiating chemotherapy ( N = 301 ) were randomly assigned to three times a week , supervised exercise of a standard dose of 25-30 min of aerobic exercise , a higher dose of 50-60 min of aerobic exercise , or a higher dose of 50-60 min of combined aerobic and resistance exercise . Outcomes were patient-reported symptoms and health-related fitness . Moderators were baseline demographic , exercise/fitness , and cancer variables . Body mass index moderated the effects of the exercise interventions on bodily pain ( P for interaction = 0.038 ) , endocrine symptoms ( P for interaction = 0.029 ) , taxane/neuropathy symptoms ( P for interaction = 0.013 ) , aerobic fitness ( P for interaction = 0.041 ) , muscular strengt

In [15]:
print("Inverted index 搜尋的時間:" + str(time_InvertedIndex) + "秒")
print("暴力搜尋時間:" + str(excute_time) + "秒")
print("相差:" + str(excute_time - time_InvertedIndex) + "秒")

Inverted index 搜尋的時間:0.6922261714935303秒
暴力搜尋時間:6.276500463485718秒
相差:5.5842742919921875秒
